In [161]:
#all imported stuff
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
%config InlineBackend.figure_format = 'svg'
from IPython.display import Audio
from scipy.signal import sawtooth, square, butter, filtfilt
from scipy.io.wavfile import read


#function that generates an oscillator
#freq in Hz
#length in seconds
#wavetype specifies the type of wave:  'sine', 'square', 'sawtooth'
#pwm is False by default, but otherwise correlates to the frequency of a pulse-width modulator.  Only active if wavetype is 'square'
#freqmod controls frequency modulation and is off by default.  Inputs to the parameter should be in the form of a list --> [<ratio of frequency modulation in float or integer form>, <modulation depth>]
#amplitude is the amplitude of the oscillator
#phi is the phase offset of the sinusoid
def genOsc(freq,length,wavetype='sine',pwm=False,freqmod=False,amplitude=1,phi=0,fs=44100):
    
    time = np.arange(0,length,1/fs)                                               #samples length of time
    
    if freqmod == False:
        modulator = np.zeros(len(time))                                           #modulator is nullified if 'freqmod' is false
    else:
        modulator = freqmod[1] * np.sin(2.0 * np.pi * (freq * freqmod[0]) * time) #create modulator signal for frequency modulation -- freqmod input is being multiplied to original frequency  
        
    w = 2 * np.pi * (freq*time+modulator) + phi                                   #frequency variable to be passed to sinusoids
        
    if wavetype == 'sine':
        osc = np.cos(w)                                                           #constructs sine wave
    
    elif wavetype == 'square':
        if pwm == False:
            osc = square(w)                                                       #constructs square wave if pulse-width modulation is false
        else:
            
            pulse = (np.sin(2*np.pi * pwm * time)*.2)+ .5 
            osc = square(w, duty=pulse)                                           #applies pulse-width modulation
            
    elif wavetype == 'sawtooth':
        osc = sawtooth(w)                                                         #constructs sawtooth wave
        
    else:
        print("Invalid wavetype.  Please select sine, square, or sawtooth.")      #error message 
        return None
    
    return(amplitude*osc)
    
    
#adsr envelope function. Outputs input(x) array with adsr envelope applied
#a,d,r in seconds
#sustain argument=desired sustain amplitude
def adsr(x,a=.1,d=.1,s=1,r=.1,fs=44100):
    if x.size<=a+d+r:
        print("Invalid adsr Input")                                             #error message
        return None

    xa= np.arange(0,a,1/fs)                                                     #sets up size of attack portion
    ya= np.linspace(0,np.max(x),xa.size)                                        #creates attack envelope
    
    xd= np.arange(a,a+d,1/fs)                                                   #sets up size of decay portion
    yd= np.linspace(np.max(x),s,xd.size)                                        #creates attack envelope
    
    xs= np.arange(a+d,a+d+(x.size/fs-a-d-r),1/fs)                               #sets up size of sustain portion
    ys= np.linspace(s,s,xs.size)                                                #creates sustain envelope
    
    xr= np.arange(a+d+(x.size/fs-a-d-r),a+d+(x.size/fs-a-d),1/fs)               #sets up size of release portion
    yr= np.linspace(s,0,xr.size)                                                #creates release envelope
    
    env=np.concatenate((ya,yd,ys,yr))                                          #creates full adsr envelope array
    adsrnote=x*env[0:x.size]                                                   #applies adsr envelope to input array
    return adsrnote


#function that creates an lfo array 
#freq in Hz
#length in seconds
def lfo(freq,length,amplitude=1,fs=44100):
    t = np.arange(0,length,1/fs)
    lfo = amplitude*np.cos(2*np.pi*freq*t)
    return lfo

#function that applies a low-pass filter
#x is the original signal
#cutoff is the cutoff frequency
#order is the order of the filter
def lowpass(x, cutoff=8000, order=10, fs=44100):
    nyq = 0.5 * fs
    normal_cutoff = cutoff / nyq

    (b,a) = butter(order, normal_cutoff, btype = 'low', analog = False)
    filt_sig = filtfilt(b,a,x)
    
    return filt_sig


#function that creates a melody
#midi is an array of MIDI values
#durations is an array of "flipped" rhythmic subdivisions, i.e. a quarter note (1/4) would be written as 4
#bpm is the desired beats per minute (tempo)
#wavetype determines the type of sinusoid.  There are three options: 'sine', 'square', and 'sawtooth'
#pwm is False by default, but otherwise correlates to the frequency difference of a pulse-width modulator.  Only active if wavetype is 'square'
#freqmod controls frequency modulation and is off by default.  Inputs to the parameter should be in the form of a list --> [<modulation frequency>, <modulation depth>]
def melody(midi, durations, bpm=60, wavetype = 'sine', pwm = False,freqmod = False, a = .01, d=.1, s=1,r = .05):
    if len(midi) != len(durations):
        print("Error! Vectors of differing lengths")        #ensures midi and durations inputs are of equal length -- errors otherwise
        return None
    
    melody = []                                             #initializes master list that will contain the melody
    for i in range(len(durations)):
        dur = ((4/durations[i])*60000/bpm)
        if midi[i]==0:
            freq=0 
        else:
            freq = (2**((midi[i]-69)/12))*440                   #converts midi into frequency values
        osc = genOsc(freq, dur/1000, wavetype, pwm,freqmod) #passes freq and dur into genOsc function to generate a sinusoid
        note = adsr(osc,a,d,s,r)                            #passes oscillator into adsr function to create envelope
        melody = np.concatenate([melody, note])             #appends note onto melody list
        
    return melody
  
#function that applies delay
#x is the original signal
#ms is length of time in milliseconds between delay onsets
#num is the number of delays
def Delay_amp(x, ms = 1000, num =3, fs = 44100):
    
    sig_list = []
    for i in range(num+1):
        amp = 1/(i+1)                                  #calculates amplitude values for each individual delay
        prepad = np.zeros(int((fs/1000)*ms*(i)))       #creates prepad of silence if necessary
        postpad = np.zeros(int((fs/1000)*ms*(num-i)))  #creates postpad of silence if necessary
        sig = np.concatenate([prepad,(amp*x),postpad]) #concatenates prepad, postpad, and delay signal together
        sig_list.append(sig)                           #appends to sig_list
        
    new_sig = np.sum(np.array(sig_list), axis = 0) #sums sig_list so that delays play simultaneously
    return(new_sig)

#function that applies tremolo via amplitude modulation
#x is the original signal
#speed is frequency of modulating signal
def Tremolo(x, speed=2, fs=44100):
    time = len(x)/fs
    t = np.arange(0,time,1/fs)
    lfo = np.sin(2*np.pi*speed*t) #creates lfo
    trem_sig = (x*lfo)            #applies lfo
    return trem_sig


In [162]:
#Melodies and length arrays
marymelody = [73,71,69,71,73,73,73,71,71,71,73,76,76]
marylengths = [8,8,8,8,8,8,4,8,8,4,8,8,4]

licmelody = [69,71,72,74,71,67,69]
liclength = [8,8,8,8,4,8,4]

mambomelody = [68,69,69,68,69,71,0,71,71,69,68,66,64]
mambolength = [8,4,8,8,4,4,8,8,8,8,4,4,4]

In [163]:
#Normal sine
x = melody(mambomelody, mambolength, 90, 'sine')
Audio(x, rate=44100)

In [164]:
#Tuba/bass
x = melody(licmelody, liclength, 100, 'sine', freqmod = [.7,1])
Audio(x, rate=44100)

In [165]:
#Inharmonic -- Ring Modulation-ish
x = melody(mambomelody, mambolength, 100, 'sine', freqmod = [.7813,1])
Audio(x, rate=44100)

In [156]:
#Mid-rangey horn
x = melody(mambomelody, mambolength, 100, 'sine', freqmod = [1, .5])
Audio(x, rate=44100)

In [166]:
#Pulse-width Square
x = melody(mambomelody, mambolength, 100, 'square', pwm = 8)
Audio(x, rate=44100)

In [174]:
#Pulse-width and Frequency Modulated Square
x = melody(mambomelody, mambolength, 100, 'square', pwm = 5, freqmod = [1.6, 1])
Audio(x, rate=44100)

In [175]:
#Tremolo -- Amplitude Modulation
sig_Trem = Tremolo(x, 6)
Audio(sig_Trem, rate=44100)

In [160]:
#Lowpass filter
sig_Filter = lowpass(x,2000)
Audio(sig_Filter, rate=44100)

In [121]:
#Delay Function
sig_Delay = Delay_amp(x, 100, 20)
Audio(sig_Delay, rate = 44100)